In [ ]:
#soundtrack - a datetime based music player
from soundtrack import *
import time
import sqlite3
from IPython.display import clear_output
import IPython
from datetime import datetime, timedelta
import pickle
import datetime as dt

db="soundtrack.db"
filename='music_dict.p'
buffer_sleep=0 #use if laggy connection to prevent STs from get skipped.
update_bit=0
try:
    music_dict=music_dict
    print("*******No DB call needed*********")
except:
    print("*******DB call needed*********")
    music_dict=getMusicDicts()    
while datetime.now().hour < 24:
    for song in music_dict:
        b=song[1][2]
        current_datetime=datetime.now().strftime('%A %H:%M:%S')
        print("Current Time:{}".format(current_datetime))
        table='song_schedule'
        current_dow=datetime.now().strftime('%w')
        current_time=datetime.now().strftime('%H:%M:%S')
        statement="SELECT * FROM {} WHERE dow='{}' AND time >'{}' ORDER BY dow ASC, time ASC LIMIT 0,1".format(table,current_dow,current_time)
        con = sqlite3.connect(db)
        cursor=con.execute(statement)
        rows = cursor.fetchall()
        for row in rows:
            next_song_time=datetime.strptime(row[1],'%H:%M:%S').time()
        song_dt = dt.datetime.combine(dt.date.today(), next_song_time)
        now=dt.datetime.now()
        difference=song_dt-now
        difference=difference.seconds
        print("{} seconds until next Soundtrack song.".format(difference))
        #time algos
        if difference < 60: #play ST song
            getNearbySchedule(current_dow,current_time)
            print("Less than 60 seconds")
            print("Difference is: {}".format(difference))
            if (difference > 10): #10 once the below proves working remove print statements 20190822
                print("!!!!!!!!!!!!!!!Opportunity to do add new songs to DB!!!!!!!!!!!!")
                new_files=getDBStatus()
                print(new_files)
                print("Update bit: {}".format(update_bit))
                if new_files:
                    addToDB()
                else:
                    time.sleep(difference/2) #play sooner. maybe /2 half if sometimes wait seems tooo long
                update_bit=1            
            song="/home/pi/Music/"+row[2]
            b=float(getMediaDuration(song))
            print("Now Playing SoundTrack \n  {} is {} seconds.".format(song,b))
            IPython.display.display(IPython.display.Audio(song,autoplay=True, embed=None))            
            time.sleep(b+buffer_sleep+2) #an additional 2 seconds for STs to play until the end
            clear_output()
            break
        elif difference < 300: #find a shuffle song that fits this short gap before next ST
            if 1 < difference-b <= 15:
                getNearbySchedule(current_dow,current_time)
                music_dict.remove(song) #remove shuffle song about to play so that next time start program it skips
                #IPython.display.display(IPython.display.Audio(song[0],autoplay=True, embed=None))
                try:
                    IPython.display.display(IPython.display.Audio(song[0],autoplay=True, embed=None))
                except ValueError:
                    #remove missing song from shuffle_count
                    table='shuffle_count'
                    statement ='DELETE FROM {} WHERE name="{}"'.format(table,song[0])
                    con.execute(statement)
                    con.commit()
                    con.close()
                    print(statement)
                    break
                print("Now Playing(pre-SoundTrack): {} : {} seconds : ".format(getMediaName(song[0]),b), end="")
                next_tm = datetime.now() + timedelta(0,float(b))
                print("Ends @ {}".format(next_tm.time()))
                statement=getShuffleCountExists(song[0])
                print(statement)
                con.execute(statement)
                con.commit()
                con.close()
                time.sleep(b+buffer_sleep)
                clear_output()
                break
        elif b < difference: #play shuffle song  
            music_dict.remove(song)
            getNearbySchedule(current_dow,current_time)
            #IPython.display.display(IPython.display.Audio(song[0],autoplay=True, embed=None))
            try:
                IPython.display.display(IPython.display.Audio(song[0],autoplay=True, embed=None))
            except ValueError:
                #remove missing song from shuffle_count
                table='shuffle_count'
                statement ='DELETE FROM {} WHERE name="{}"'.format(table,song[0])
                con.execute(statement)
                con.commit()
                con.close()
                print(statement)
                break
            print("Now Playing: {} : {} seconds : ".format(getMediaName(song[0]),b), end="")
            next_tm = datetime.now() + timedelta(0,float(b))
            print("Ends @ {}".format(next_tm.time()))
            statement=getShuffleCountExists(song[0])
            print(statement)
            con.execute(statement)
            con.commit()
            con.close()
            time.sleep(b+buffer_sleep)
        clear_output()

Current Time:Thursday 22:37:03
476 seconds until next Soundtrack song.
22:00:00: shuffle_exclude/go_betweens-Quiet Heart.mp3
22:15:00: coldplay-LifeInTechnicolor.mp3
22:30:00: shuffle_exclude/teenage_fanclub-Only_With_You.mp3
Next: 22:45:00: sun_kil_moon-Glenn Tipton.mp3
23:00:00: shuffle_exclude/teenage_fanclub-Cells.mp3
23:07:30: shuffle_exclude/Ryan_Adams_-_Bad_Blood_from_1989_Official_Audio.mp3


Now Playing: Grandmaster_Flash_The_Furious_Five_-_The_Message_Official_Video.mp3 : 359 seconds : Ends @ 22:43:03.414488
UPDATE shuffle_count SET cnt=22,time="2019-08-22 22:37:04" WHERE name="/home/pi/Music/Grandmaster_Flash_The_Furious_Five_-_The_Message_Official_Video.mp3"


In [ ]:
print(music_dict)

In [2]:
print(update_bit)

1
